### Open WRF output file and read some variables

In [ ]:
import numpy, Nio, Ngl, os

filename = "../Data/wrfout_d03_2012-04-22_23_00_00.nc"
f  = Nio.open_file(filename,"w")      # Open WRF output file as "write"
T  = f.variables["T"]                 # potential temperature
P  = f.variables["P"]                 # perturbation pressure
PB = f.variables["PB"]                # base pressure
print T     # These are NioVariable objects
print P
print PB

### Calculate temperature from T, P, PB using "wrf_tk" function

In [ ]:
THETA = T[:] + 300          # perturbation + reference temperature
PPB   = P[:] + PB[:]
TK    = Ngl.wrf_tk(PPB, THETA)

print "TK min/max = %g / %g" % (numpy.min(TK[:]),numpy.max(TK[:]))

# Write TK to same NetCDF file

### Define variable on file using another variable's dimensions

In [ ]:
new_var_name = "TK"
f.create_variable(new_var_name,'d',T.dimensions)

### Write attributes of variable to file, changing "description" and "units"

In [ ]:
varAtts = T.__dict__.keys()    # Get all of T's attributes
varAtts.sort()
for att in varAtts:
    if att is "description":
        value = "Temperature"
    elif att is "units":
        value = "degK"      # Better than just "K"
    else:
        value = getattr(T,att)
        
    setattr(f.variables[new_var_name],att,value)   # Write attribute and value to file

### Write data values to file and close it

In [ ]:
f.variables[new_var_name].assign_value(TK)
f.close()

### Reopen file and print it

In [ ]:
f2 = Nio.open_file(filename,"r")
print f2

### Read TK

In [ ]:
tk = f2.variables["TK"]
print "TK after reading back in: %g / %g" % (numpy.min(tk[:]),numpy.max(tk[:]))
print TK.shape

### Plot TK directly from file

In [ ]:
from wrf_plot_ngl import *
wrf_plot_from_file(filename,"TK")
from IPython.display import Image
Image(filename='wrfplot.png')